In [70]:
# imports
import pandas as pd
import numpy as np

from great_schools import get_nearby_schools
from distance import get_distance
from secret import get_key


## Shaun and Daniela's Boston Public School Analysis
#### 2021.04.10

Fetch the API key from the local filesystem.

In [71]:
# get the API key
api_key_file = '../keys/api.key'
api_key = get_key(api_key_file)

Use the `nearby_schools` API endpoint to grab raw data of all schools within the maximum radius

In [72]:
# Some columns will dropped immediately as pre-processing.
drops = [
    'nces-id',
    'school-summary',
    'street',
    'fipscounty',
    'phone',
    'fax',
    'web-site',
    'overview-url',
    'rating-description',
    'distance',
]

# Grab data for Boston.
refresh = False
boston_nearby_schools_file = '../data/nearby_schools/boston.csv'
if refresh:
    boston_schools = get_nearby_schools(api_key,"42.3","-71.2","50")
    boston_df = pd.DataFrame.from_dict(boston_schools)
    boston_df.drop(columns=drops,inplace=True)
    boston_df.to_csv(boston_nearby_schools_file, )
else:
    boston_df = pd.read_csv(boston_nearby_schools_file)
    boston_df.set_index(keys=["universal-id"], drop=True, inplace=True)
    boston_df.drop(columns=["Unnamed: 0"], inplace=True)

# Grab data for Buffalo.
refresh = False
buffalo_nearby_schools_file = '../data/nearby_schools/buffalo.csv'
if refresh:
    buffalo_schools = get_nearby_schools(api_key,"42.9625","-78.7425","50")
    buffalo_df = pd.DataFrame.from_dict(buffalo_schools)
    buffalo_df.drop(columns=drops,inplace=True)
    buffalo_df.to_csv(buffalo_nearby_schools_file)
else:
    buffalo_df = pd.read_csv(buffalo_nearby_schools_file)
    buffalo_df.set_index(keys=["universal-id"], drop=True, inplace=True)
    buffalo_df.drop(columns=["Unnamed: 0"], inplace=True)

Process the `lat` and `lon` columns from the API output into tuples.

Then create two new columns:
- Distance to Downtown
- Distance to Work

In [73]:
# Form tuple to represent coordinates
boston_df['coordinates'] = list(zip(boston_df.lat,boston_df.lon))
#boston_df.drop(columns=['lat', 'lon'], inplace=True)

# Define coordinates of important places
downtown=(42.3674836866797, -71.07134540735377) # Science Museum
work=(42.47381059540949, -71.25414135292398) # Hartwell

# Create new columns to tabulate distance to these important places
boston_df['distance-to-downtown'] = boston_df['coordinates'].apply(func=get_distance,p2=downtown)
boston_df['distance-to-work'] = boston_df['coordinates'].apply(func=get_distance,p2=work)

For Boston, drop all schools that aren't in Massachusetts.

In [74]:
boston_df = boston_df[boston_df['state'] == "MA"]

boston_df.sample(5)

state-id                                     name    type  \
universal-id                                                              
2501042        7050505          Masconomet Regional High School  public   
2500337         350380  Young Achievers Science and Math School  public   
2500402         440017            Kennedy K-5 Elementary School  public   
2501682        3070010                                   Boyden  public   
2501507        2760305          P. Brent Trottier Middle School  public   

             level-codes                  level          city state   zip  \
universal-id                                                                
2501042                h             9,10,11,12       Boxford    MA  1921   
2500337            p,e,m  PK,KG,1,2,3,4,5,6,7,8      Mattapan    MA  2126   
2500402                e           KG,1,2,3,4,5      Brockton    MA  2301   
2501682                e           KG,1,2,3,4,5       Walpole    MA  2071   
2501507                m                  6,7,8  Southborough    MA  1772   

                        county        lat        lon  \
universal-id                                           
2501042           Essex County  42.627754 -70.974693   
2500337         Suffolk County  42.282269 -71.095016   
2500402        Plymouth County  42.059696 -71.037262   
2501682         Norfolk County  42.105808 -71.258743   
2501507       Worcester County  42.299240 -71.542259   

                             district-name  district-id  rating    year  \
universal-id                                                              
2501042         Masconomet School District          259     8.0  2021.0   
2500337             Boston School District           99     2.0  2021.0   
2500402           Brockton School District          111     4.0  2021.0   
2501682            Walpole School District          426     6.0  2021.0   
2501507       Southborough School District          387     8.0  2021.0   

                          coordinates  distance-to-downtown  distance-to-work  
universal-id                                                                   
2501042       (42.627754, -70.974693)             30.005931         28.583420  
2500337       (42.282269, -71.095016)              9.673200         24.989359  
2500402       (42.059696, -71.037262)             34.339345         49.384728  
2501682       (42.105808, -71.258743)             32.933990         40.921772  
2501507        (42.29924, -71.542259)             39.445654         30.606258